<a href="https://colab.research.google.com/github/jubiology/misc/blob/main/H12stats_Burkina.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
%pip install -q --no-warn-conflicts malariagen_data
import warnings
warnings.simplefilter(action='ignore', category=Warning)
import malariagen_data
import numpy as np
import pandas as pd
import os
import nbconvert

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 165.1/165.1 kB 2.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.2/3.2 MB 13.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 35.8/35.8 MB 14.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.5/7.5 MB 29.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 4.0/4.0 MB 23.0 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 302.5/302.5 kB 9.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 141.1/141.1 kB 1.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 24.4/24.4 MB 17.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 8.1/8.1 MB 23.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 210.2/210.2 kB 20.2 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 8.6/8.6 MB 33.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━

In [2]:
try:
    from google.colab import drive
    drive.mount("drive")
except ImportError:
    pass

Mounted at drive


define directory within google drive as data cache

In [3]:
results_dir = "drive/MyDrive/eQTL/malariagen_H12_stats"

In [4]:
ag3 = malariagen_data.Ag3(results_cache=results_dir)
ag3

<MalariaGEN Ag3 API client>
Storage URL             : gs://vo_agam_release/
Data releases available : 3.0, 3.1, 3.2, 3.3, 3.4, 3.5, 3.6, 3.7, 3.8, 3.9, 3.10
Results cache           : /content/drive/MyDrive/eQTL/malariagen_H12_stats
Cohorts analysis        : 20240418
AIM analysis            : 20220528
Site filters analysis   : dt_20200416
Software version        : malariagen_data 11.0.0
Client location         : South Carolina, United States (Google Cloud us-east1)
---
Please note that data are subject to terms of use,
for more information see https://www.malariagen.net/data
or contact support@malariagen.net. For API documentation see 
https://malariagen.github.io/malariagen-data-python/v11.0.0/Ag3.html

define sample sets

In [5]:
sample_sets = ["AG1000G-BF-A", "AG1000G-BF-B", "AG1000G-BF-C"]

# Coluzzii
## 2L

In [6]:
sample_query="cohort_admin2_year == ['BF-09_Houet_colu_2014', 'BF-09_Houet_colu_2012']"
contig="2L"

In [7]:
ag3.plot_h12_calibration(
    contig=contig,
    sample_sets=sample_sets,
    sample_query=sample_query,
)

In [8]:
window=1000

In [9]:
ag3.plot_h12_gwss(
    contig=contig,
    window_size=window,
    sample_sets=sample_sets,
    sample_query=sample_query,
)

In [10]:
# Parameters
output_file_path = os.path.join(results_dir, 'H12stats_coluzzii_Chr2L.tsv')
outliers_file_path = os.path.join(results_dir, 'H12stats_95qoutliers_coluzzii_Chr2L.tsv')


# Perform H12 calculation
h12counts = ag3.h12_gwss(
    contig=contig,
    sample_sets=sample_sets,
    sample_query=sample_query,
    window_size=window,
)

# Initialize an empty list to store the results
results = []

# Process h12counts based on its actual type and structure
if isinstance(h12counts, tuple):
    window_positions, h12_values = h12counts
    # Convert window positions to integers
    window_positions = window_positions.astype(int)
else:
    print("Unexpected h12counts format")

# Calculate start and end positions based on the window size
start_positions = window_positions - (window // 2)
end_positions = window_positions + (window // 2)

# Save the results to the output file in tabular format with headers and contig name
with open(output_file_path, 'w') as file:
    # Write the headers
    file.write("chr\tstart\tend\tmid\tH12\n")
    # Write data
    for start, end, mid, h12 in zip(start_positions, end_positions, window_positions, h12_values):
        file.write(f"{contig}\t{start}\t{end}\t{mid}\t{h12}\n")

print(f"Results saved to {output_file_path}")

# Load the results into a DataFrame
df = pd.read_csv(output_file_path, delimiter='\t')

# Compute the 95th percentile for H12 values
threshold = np.percentile(df['H12'], 95)

# Filter the DataFrame to get the top 5% H12 values
outliers_df = df[df['H12'] >= threshold]

# Save the outliers to a new file
outliers_df.to_csv(outliers_file_path, sep='\t', index=False)

print(f"Outliers saved to {outliers_file_path}")

Results saved to drive/MyDrive/eQTL/malariagen_H12_stats/H12stats_coluzzii_Chr2L.tsv
Outliers saved to drive/MyDrive/eQTL/malariagen_H12_stats/H12stats_95qoutliers_coluzzii_Chr2L.tsv


# COLUZZII
# 2R

In [11]:
sample_query="cohort_admin2_year == ['BF-09_Houet_colu_2014', 'BF-09_Houet_colu_2012']"
contig="2R"

In [12]:
ag3.plot_h12_calibration(
    contig=contig,
    sample_sets=sample_sets,
    sample_query=sample_query,
)

In [13]:
window=1000

In [14]:
ag3.plot_h12_gwss(
    contig=contig,
    window_size=window,
    sample_sets=sample_sets,
    sample_query=sample_query,
)

In [15]:
# Parameters
output_file_path = os.path.join(results_dir, 'H12stats_coluzzii_Chr2R.tsv')
outliers_file_path = os.path.join(results_dir, 'H12stats_95qoutliers_coluzzii_Chr2R.tsv')


# Perform H12 calculation
h12counts = ag3.h12_gwss(
    contig=contig,
    sample_sets=sample_sets,
    sample_query=sample_query,
    window_size=window,
)

# Initialize an empty list to store the results
results = []

# Process h12counts based on its actual type and structure
if isinstance(h12counts, tuple):
    window_positions, h12_values = h12counts
    # Convert window positions to integers
    window_positions = window_positions.astype(int)
else:
    print("Unexpected h12counts format")

# Calculate start and end positions based on the window size
start_positions = window_positions - (window // 2)
end_positions = window_positions + (window // 2)

# Save the results to the output file in tabular format with headers and contig name
with open(output_file_path, 'w') as file:
    # Write the headers
    file.write("chr\tstart\tend\tmid\tH12\n")
    # Write data
    for start, end, mid, h12 in zip(start_positions, end_positions, window_positions, h12_values):
        file.write(f"{contig}\t{start}\t{end}\t{mid}\t{h12}\n")

print(f"Results saved to {output_file_path}")

# Load the results into a DataFrame
df = pd.read_csv(output_file_path, delimiter='\t')

# Compute the 95th percentile for H12 values
threshold = np.percentile(df['H12'], 95)

# Filter the DataFrame to get the top 5% H12 values
outliers_df = df[df['H12'] >= threshold]

# Save the outliers to a new file
outliers_df.to_csv(outliers_file_path, sep='\t', index=False)

print(f"Outliers saved to {outliers_file_path}")

Results saved to drive/MyDrive/eQTL/malariagen_H12_stats/H12stats_coluzzii_Chr2R.tsv
Outliers saved to drive/MyDrive/eQTL/malariagen_H12_stats/H12stats_95qoutliers_coluzzii_Chr2R.tsv


# COLUZZII
# 3L

In [16]:
sample_query="cohort_admin2_year == ['BF-09_Houet_colu_2014', 'BF-09_Houet_colu_2012']"
contig="3L"

In [17]:
ag3.plot_h12_calibration(
    contig=contig,
    sample_sets=sample_sets,
    sample_query=sample_query,
)

In [18]:
window=1000

In [19]:
ag3.plot_h12_gwss(
    contig=contig,
    window_size=window,
    sample_sets=sample_sets,
    sample_query=sample_query,
)

In [20]:
# Parameters
output_file_path = os.path.join(results_dir, 'H12stats_coluzzii_Chr3L.tsv')
outliers_file_path = os.path.join(results_dir, 'H12stats_95qoutliers_coluzzii_Chr3L.tsv')


# Perform H12 calculation
h12counts = ag3.h12_gwss(
    contig=contig,
    sample_sets=sample_sets,
    sample_query=sample_query,
    window_size=window,
)

# Initialize an empty list to store the results
results = []

# Process h12counts based on its actual type and structure
if isinstance(h12counts, tuple):
    window_positions, h12_values = h12counts
    # Convert window positions to integers
    window_positions = window_positions.astype(int)
else:
    print("Unexpected h12counts format")

# Calculate start and end positions based on the window size
start_positions = window_positions - (window // 2)
end_positions = window_positions + (window // 2)

# Save the results to the output file in tabular format with headers and contig name
with open(output_file_path, 'w') as file:
    # Write the headers
    file.write("chr\tstart\tend\tmid\tH12\n")
    # Write data
    for start, end, mid, h12 in zip(start_positions, end_positions, window_positions, h12_values):
        file.write(f"{contig}\t{start}\t{end}\t{mid}\t{h12}\n")

print(f"Results saved to {output_file_path}")

# Load the results into a DataFrame
df = pd.read_csv(output_file_path, delimiter='\t')

# Compute the 95th percentile for H12 values
threshold = np.percentile(df['H12'], 95)

# Filter the DataFrame to get the top 5% H12 values
outliers_df = df[df['H12'] >= threshold]

# Save the outliers to a new file
outliers_df.to_csv(outliers_file_path, sep='\t', index=False)

print(f"Outliers saved to {outliers_file_path}")

Results saved to drive/MyDrive/eQTL/malariagen_H12_stats/H12stats_coluzzii_Chr3L.tsv
Outliers saved to drive/MyDrive/eQTL/malariagen_H12_stats/H12stats_95qoutliers_coluzzii_Chr3L.tsv


# COLUZZII
# 3R

In [21]:
sample_query="cohort_admin2_year == ['BF-09_Houet_colu_2014', 'BF-09_Houet_colu_2012']"
contig="3R"

In [22]:
ag3.plot_h12_calibration(
    contig=contig,
    sample_sets=sample_sets,
    sample_query=sample_query,
)

In [23]:
window=1000

In [24]:
ag3.plot_h12_gwss(
    contig=contig,
    window_size=window,
    sample_sets=sample_sets,
    sample_query=sample_query,
)

In [25]:
# Parameters
output_file_path = os.path.join(results_dir, 'H12stats_coluzzii_Chr3R.tsv')
outliers_file_path = os.path.join(results_dir, 'H12stats_95qoutliers_coluzzii_Chr3R.tsv')


# Perform H12 calculation
h12counts = ag3.h12_gwss(
    contig=contig,
    sample_sets=sample_sets,
    sample_query=sample_query,
    window_size=window,
)

# Initialize an empty list to store the results
results = []

# Process h12counts based on its actual type and structure
if isinstance(h12counts, tuple):
    window_positions, h12_values = h12counts
    # Convert window positions to integers
    window_positions = window_positions.astype(int)
else:
    print("Unexpected h12counts format")

# Calculate start and end positions based on the window size
start_positions = window_positions - (window // 2)
end_positions = window_positions + (window // 2)

# Save the results to the output file in tabular format with headers and contig name
with open(output_file_path, 'w') as file:
    # Write the headers
    file.write("chr\tstart\tend\tmid\tH12\n")
    # Write data
    for start, end, mid, h12 in zip(start_positions, end_positions, window_positions, h12_values):
        file.write(f"{contig}\t{start}\t{end}\t{mid}\t{h12}\n")

print(f"Results saved to {output_file_path}")

# Load the results into a DataFrame
df = pd.read_csv(output_file_path, delimiter='\t')

# Compute the 95th percentile for H12 values
threshold = np.percentile(df['H12'], 95)

# Filter the DataFrame to get the top 5% H12 values
outliers_df = df[df['H12'] >= threshold]

# Save the outliers to a new file
outliers_df.to_csv(outliers_file_path, sep='\t', index=False)

print(f"Outliers saved to {outliers_file_path}")

Results saved to drive/MyDrive/eQTL/malariagen_H12_stats/H12stats_coluzzii_Chr3R.tsv
Outliers saved to drive/MyDrive/eQTL/malariagen_H12_stats/H12stats_95qoutliers_coluzzii_Chr3R.tsv


# COLUZZII
# X

In [26]:
sample_query="cohort_admin2_year == ['BF-09_Houet_colu_2014', 'BF-09_Houet_colu_2012']"
contig="X"

In [27]:
ag3.plot_h12_calibration(
    contig=contig,
    sample_sets=sample_sets,
    sample_query=sample_query,
)

In [28]:
window=5000

In [29]:
ag3.plot_h12_gwss(
    contig=contig,
    window_size=window,
    sample_sets=sample_sets,
    sample_query=sample_query,
)

In [30]:
# Parameters
output_file_path = os.path.join(results_dir, 'H12stats_coluzzii_ChrX.tsv')
outliers_file_path = os.path.join(results_dir, 'H12stats_95qoutliers_coluzzii_ChrX.tsv')


# Perform H12 calculation
h12counts = ag3.h12_gwss(
    contig=contig,
    sample_sets=sample_sets,
    sample_query=sample_query,
    window_size=window,
)

# Initialize an empty list to store the results
results = []

# Process h12counts based on its actual type and structure
if isinstance(h12counts, tuple):
    window_positions, h12_values = h12counts
    # Convert window positions to integers
    window_positions = window_positions.astype(int)
else:
    print("Unexpected h12counts format")

# Calculate start and end positions based on the window size
start_positions = window_positions - (window // 2)
end_positions = window_positions + (window // 2)

# Save the results to the output file in tabular format with headers and contig name
with open(output_file_path, 'w') as file:
    # Write the headers
    file.write("chr\tstart\tend\tmid\tH12\n")
    # Write data
    for start, end, mid, h12 in zip(start_positions, end_positions, window_positions, h12_values):
        file.write(f"{contig}\t{start}\t{end}\t{mid}\t{h12}\n")

print(f"Results saved to {output_file_path}")

# Load the results into a DataFrame
df = pd.read_csv(output_file_path, delimiter='\t')

# Compute the 95th percentile for H12 values
threshold = np.percentile(df['H12'], 95)

# Filter the DataFrame to get the top 5% H12 values
outliers_df = df[df['H12'] >= threshold]

# Save the outliers to a new file
outliers_df.to_csv(outliers_file_path, sep='\t', index=False)

print(f"Outliers saved to {outliers_file_path}")

Results saved to drive/MyDrive/eQTL/malariagen_H12_stats/H12stats_coluzzii_ChrX.tsv
Outliers saved to drive/MyDrive/eQTL/malariagen_H12_stats/H12stats_95qoutliers_coluzzii_ChrX.tsv


# GAMBIAE
## 2L

In [31]:
sample_query="cohort_admin2_year == ['BF-09_Houet_gamb_2014', 'BF-09_Houet_gamb_2012']"
contig="2L"

In [32]:
ag3.plot_h12_calibration(
    contig=contig,
    sample_sets=sample_sets,
    sample_query=sample_query,
)

In [33]:
window=2500

In [34]:
ag3.plot_h12_gwss(
    contig=contig,
    window_size=window,
    sample_sets=sample_sets,
    sample_query=sample_query,
)

In [35]:
# Parameters
output_file_path = os.path.join(results_dir, 'H12stats_gambiae_Chr2L.tsv')
outliers_file_path = os.path.join(results_dir, 'H12stats_95qoutliers_gambiae_Chr2L.tsv')

# Perform H12 calculation
h12counts = ag3.h12_gwss(
    contig=contig,
    sample_sets=sample_sets,
    sample_query=sample_query,
    window_size=window,
)

# Initialize an empty list to store the results
results = []

# Process h12counts based on its actual type and structure
if isinstance(h12counts, tuple):
    window_positions, h12_values = h12counts
    # Convert window positions to integers
    window_positions = window_positions.astype(int)
else:
    print("Unexpected h12counts format")

# Calculate start and end positions based on the window size
start_positions = window_positions - (window // 2)
end_positions = window_positions + (window // 2)

# Save the results to the output file in tabular format with headers and contig name
with open(output_file_path, 'w') as file:
    # Write the headers
    file.write("chr\tstart\tend\tmid\tH12\n")
    # Write data
    for start, end, mid, h12 in zip(start_positions, end_positions, window_positions, h12_values):
        file.write(f"{contig}\t{start}\t{end}\t{mid}\t{h12}\n")

print(f"Results saved to {output_file_path}")

# Load the results into a DataFrame
df = pd.read_csv(output_file_path, delimiter='\t')

# Compute the 95th percentile for H12 values
threshold = np.percentile(df['H12'], 95)

# Filter the DataFrame to get the top 5% H12 values
outliers_df = df[df['H12'] >= threshold]

# Save the outliers to a new file
outliers_df.to_csv(outliers_file_path, sep='\t', index=False)

print(f"Outliers saved to {outliers_file_path}")

Results saved to drive/MyDrive/eQTL/malariagen_H12_stats/H12stats_gambiae_Chr2L.tsv
Outliers saved to drive/MyDrive/eQTL/malariagen_H12_stats/H12stats_95qoutliers_gambiae_Chr2L.tsv


# GAMBIAE
## 2R
figure out window size

In [36]:
sample_query="cohort_admin2_year == ['BF-09_Houet_gamb_2014', 'BF-09_Houet_gamb_2012']"
contig="2R"

In [37]:
ag3.plot_h12_calibration(
    contig=contig,
    sample_sets=sample_sets,
    sample_query=sample_query,
)

In [38]:
window=1000

In [39]:
ag3.plot_h12_gwss(
    contig=contig,
    window_size=window,
    sample_sets=sample_sets,
    sample_query=sample_query,
)

In [40]:
# Parameters

output_file_path = os.path.join(results_dir, 'H12stats_gambiae_Chr2R.tsv')
outliers_file_path = os.path.join(results_dir, 'H12stats_95qoutliers_gambiae_Chr2R.tsv')


# Perform H12 calculation
h12counts = ag3.h12_gwss(
    contig=contig,
    sample_sets=sample_sets,
    sample_query=sample_query,
    window_size=window,
)

# Initialize an empty list to store the results
results = []

# Process h12counts based on its actual type and structure
if isinstance(h12counts, tuple):
    window_positions, h12_values = h12counts
    # Convert window positions to integers
    window_positions = window_positions.astype(int)
else:
    print("Unexpected h12counts format")

# Calculate start and end positions based on the window size
start_positions = window_positions - (window // 2)
end_positions = window_positions + (window // 2)

# Save the results to the output file in tabular format with headers and contig name
with open(output_file_path, 'w') as file:
    # Write the headers
    file.write("chr\tstart\tend\tmid\tH12\n")
    # Write data
    for start, end, mid, h12 in zip(start_positions, end_positions, window_positions, h12_values):
        file.write(f"{contig}\t{start}\t{end}\t{mid}\t{h12}\n")

print(f"Results saved to {output_file_path}")

# Load the results into a DataFrame
df = pd.read_csv(output_file_path, delimiter='\t')

# Compute the 95th percentile for H12 values
threshold = np.percentile(df['H12'], 95)

# Filter the DataFrame to get the top 5% H12 values
outliers_df = df[df['H12'] >= threshold]

# Save the outliers to a new file
outliers_df.to_csv(outliers_file_path, sep='\t', index=False)

print(f"Outliers saved to {outliers_file_path}")

Results saved to drive/MyDrive/eQTL/malariagen_H12_stats/H12stats_gambiae_Chr2R.tsv
Outliers saved to drive/MyDrive/eQTL/malariagen_H12_stats/H12stats_95qoutliers_gambiae_Chr2R.tsv


# GAMBIAE
## 3L

In [41]:
sample_query="cohort_admin2_year == ['BF-09_Houet_gamb_2014', 'BF-09_Houet_gamb_2012']"
contig="3L"

In [42]:
ag3.plot_h12_calibration(
    contig=contig,
    sample_sets=sample_sets,
    sample_query=sample_query,
)

In [43]:
window=1000

In [44]:
ag3.plot_h12_gwss(
    contig=contig,
    window_size=window,
    sample_sets=sample_sets,
    sample_query=sample_query,
)

In [45]:
# Parameters
output_file_path = os.path.join(results_dir, 'H12stats_gambiae_Chr3L.tsv')
outliers_file_path = os.path.join(results_dir, 'H12stats_95qoutliers_gambiae_Chr3L.tsv')


# Perform H12 calculation
h12counts = ag3.h12_gwss(
    contig=contig,
    sample_sets=sample_sets,
    sample_query=sample_query,
    window_size=window,
)

# Initialize an empty list to store the results
results = []

# Process h12counts based on its actual type and structure
if isinstance(h12counts, tuple):
    window_positions, h12_values = h12counts
    # Convert window positions to integers
    window_positions = window_positions.astype(int)
else:
    print("Unexpected h12counts format")

# Calculate start and end positions based on the window size
start_positions = window_positions - (window // 2)
end_positions = window_positions + (window // 2)

# Save the results to the output file in tabular format with headers and contig name
with open(output_file_path, 'w') as file:
    # Write the headers
    file.write("chr\tstart\tend\tmid\tH12\n")
    # Write data
    for start, end, mid, h12 in zip(start_positions, end_positions, window_positions, h12_values):
        file.write(f"{contig}\t{start}\t{end}\t{mid}\t{h12}\n")

print(f"Results saved to {output_file_path}")

# Load the results into a DataFrame
df = pd.read_csv(output_file_path, delimiter='\t')

# Compute the 95th percentile for H12 values
threshold = np.percentile(df['H12'], 95)

# Filter the DataFrame to get the top 5% H12 values
outliers_df = df[df['H12'] >= threshold]

# Save the outliers to a new file
outliers_df.to_csv(outliers_file_path, sep='\t', index=False)

print(f"Outliers saved to {outliers_file_path}")

Results saved to drive/MyDrive/eQTL/malariagen_H12_stats/H12stats_gambiae_Chr3L.tsv
Outliers saved to drive/MyDrive/eQTL/malariagen_H12_stats/H12stats_95qoutliers_gambiae_Chr3L.tsv


# GAMBIAE
## 3R

In [46]:
sample_query="cohort_admin2_year == ['BF-09_Houet_gamb_2014', 'BF-09_Houet_gamb_2012']"
contig="3R"

In [47]:
ag3.plot_h12_calibration(
    contig=contig,
    sample_sets=sample_sets,
    sample_query=sample_query,
)

In [48]:
window=1000

In [49]:
ag3.plot_h12_gwss(
    contig=contig,
    window_size=window,
    sample_sets=sample_sets,
    sample_query=sample_query,
)

In [50]:
# Parameters
output_file_path = os.path.join(results_dir, 'H12stats_gambiae_Chr3R.tsv')
outliers_file_path = os.path.join(results_dir, 'H12stats_95qoutliers_gambiae_Chr3R.tsv')


# Perform H12 calculation
h12counts = ag3.h12_gwss(
    contig=contig,
    sample_sets=sample_sets,
    sample_query=sample_query,
    window_size=window,
)

# Initialize an empty list to store the results
results = []

# Process h12counts based on its actual type and structure
if isinstance(h12counts, tuple):
    window_positions, h12_values = h12counts
    # Convert window positions to integers
    window_positions = window_positions.astype(int)
else:
    print("Unexpected h12counts format")

# Calculate start and end positions based on the window size
start_positions = window_positions - (window // 2)
end_positions = window_positions + (window // 2)

# Save the results to the output file in tabular format with headers and contig name
with open(output_file_path, 'w') as file:
    # Write the headers
    file.write("chr\tstart\tend\tmid\tH12\n")
    # Write data
    for start, end, mid, h12 in zip(start_positions, end_positions, window_positions, h12_values):
        file.write(f"{contig}\t{start}\t{end}\t{mid}\t{h12}\n")

print(f"Results saved to {output_file_path}")

# Load the results into a DataFrame
df = pd.read_csv(output_file_path, delimiter='\t')

# Compute the 95th percentile for H12 values
threshold = np.percentile(df['H12'], 95)

# Filter the DataFrame to get the top 5% H12 values
outliers_df = df[df['H12'] >= threshold]

# Save the outliers to a new file
outliers_df.to_csv(outliers_file_path, sep='\t', index=False)

print(f"Outliers saved to {outliers_file_path}")

Results saved to drive/MyDrive/eQTL/malariagen_H12_stats/H12stats_gambiae_Chr3R.tsv
Outliers saved to drive/MyDrive/eQTL/malariagen_H12_stats/H12stats_95qoutliers_gambiae_Chr3R.tsv


# GAMBIAE
## X

In [51]:
sample_query="cohort_admin2_year == ['BF-09_Houet_gamb_2014', 'BF-09_Houet_gamb_2012']"
contig="X"

In [52]:
ag3.plot_h12_calibration(
    contig=contig,
    sample_sets=sample_sets,
    sample_query=sample_query,
)

In [53]:
window=2500

In [54]:
ag3.plot_h12_gwss(
    contig=contig,
    window_size=window,
    sample_sets=sample_sets,
    sample_query=sample_query,
)

In [55]:
# Parameters
output_file_path = os.path.join(results_dir, 'H12stats_gambiae_ChrX.tsv')
outliers_file_path = os.path.join(results_dir, 'H12stats_95qoutliers_gambiae_ChrX.tsv')


# Perform H12 calculation
h12counts = ag3.h12_gwss(
    contig=contig,
    sample_sets=sample_sets,
    sample_query=sample_query,
    window_size=window,
)

# Initialize an empty list to store the results
results = []

# Process h12counts based on its actual type and structure
if isinstance(h12counts, tuple):
    window_positions, h12_values = h12counts
    # Convert window positions to integers
    window_positions = window_positions.astype(int)
else:
    print("Unexpected h12counts format")

# Calculate start and end positions based on the window size
start_positions = window_positions - (window // 2)
end_positions = window_positions + (window // 2)

# Save the results to the output file in tabular format with headers and contig name
with open(output_file_path, 'w') as file:
    # Write the headers
    file.write("chr\tstart\tend\tmid\tH12\n")
    # Write data
    for start, end, mid, h12 in zip(start_positions, end_positions, window_positions, h12_values):
        file.write(f"{contig}\t{start}\t{end}\t{mid}\t{h12}\n")

print(f"Results saved to {output_file_path}")

# Load the results into a DataFrame
df = pd.read_csv(output_file_path, delimiter='\t')

# Compute the 95th percentile for H12 values
threshold = np.percentile(df['H12'], 95)

# Filter the DataFrame to get the top 5% H12 values
outliers_df = df[df['H12'] >= threshold]

# Save the outliers to a new file
outliers_df.to_csv(outliers_file_path, sep='\t', index=False)

print(f"Outliers saved to {outliers_file_path}")

Results saved to drive/MyDrive/eQTL/malariagen_H12_stats/H12stats_gambiae_ChrX.tsv
Outliers saved to drive/MyDrive/eQTL/malariagen_H12_stats/H12stats_95qoutliers_gambiae_ChrX.tsv


In [56]:
%cd /content/drive/MyDrive/Colab\ Notebooks/


/content/drive/MyDrive/Colab Notebooks


In [57]:
# Step 2: Convert the notebook to HTML
# Define the filename
notebook_filename = "H12stats_Burkina.ipynb"
html_filename = notebook_filename.replace(".ipynb", ".html")

# Save the notebook
!jupyter nbconvert --to html "{notebook_filename}"

# Step 3: Download the HTML file
from google.colab import files

# Download the HTML file
files.download(html_filename)

[NbConvertApp] Converting notebook H12stats_Burkina.ipynb to html
[NbConvertApp] Writing 707196 bytes to H12stats_Burkina.html


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>